# Interactive Map - Folium (Leaflet)

For experimentation on creating an interactive map with our data.

In [1]:
### Import Libraries

# File manipulation

import os # For working with Operating System
from sys import platform # Diagnose operating system
import json # For working with Json files
import requests # Processing online requests


# Analysis

import numpy as np # For working with Arrays
import pandas as pd # Data Manipulation
import geopandas as gpd # Spatial Data Manipulation

# Visualization

import folium # Interactive Leaflet.js mapping 
from folium import features

import warnings
warnings.filterwarnings('ignore') # Ignores some warnings

In [2]:
### Definitions

cwd = os.getcwd() # Current Working Directory

# Forward or back slashs for filepaths? <- Not sure here. Only know Windows & Linux

if platform == "linux" or platform == "linux2":
    slash = '/'
elif platform == 'win32':
    slash = '\\'

# Load Data

In [3]:
# Load Data

# Get GeoJsons from GitHub

# Base URL

url = (
    "https://raw.githubusercontent.com/RwHendrickson/MappingGZ/main/Prototype/Notebooks/CleaningData"
)

# Minneapolis Boundary

mpls_boundary_path = f"{url}/Boundary/mpls_boundaryWGS84.geojson"

# GZ Boundaries

gz_boundary_path = f"{url}/GZ_Boundaries/gz_boundaryWGS84.geojson"

# Get bigger files from computer

cwd = os.getcwd()

mpls_aadt_path = cwd + slash + 'CleaningData' + slash + 'Traffic' + slash + 'mpls_aadtWGS84.geojson'
mpls_emissions_path = cwd + slash + 'CleaningData' + slash + 'PermittedEmissions' + slash + 'mpls_emissions.csv'
mpls_health_path = cwd + slash + 'CleaningData' + slash + 'Health' + slash + 'mpls_health_tracts' + slash + 'mpls_health_tracts.shp'
mpls_census_path = cwd + slash + 'CleaningData' + slash + 'Demographics' + slash + 'mpls_census_data' + slash + 'mpls_census_data.shp'

# Load files as geodataframes for focusing data

#traffic = gpd.read_file(mpls_aadt_path)
#emissions = pd.read_csv(mpls_emissions_path)
#health = gpd.read_file(mpls_health_path)
#demo = gpd.read_file(mpls_census_path)

#emissions_geo = gpd.GeoDataFrame(emissions, geometry = gpd.points_from_xy(emissions.LONGITUDE, emissions.LATITUDE, crs = 'EPSG:4326'))

In [4]:
traffic = gpd.read_file('mpls_aadtWGS84.geojson')
emissions = pd.read_csv('mpls_emissions.csv')
health = gpd.read_file('DONE/mpls_health_tracts.shp')
demo = gpd.read_file('DONE/mpls_census_data.shp')

emissions_geo = gpd.GeoDataFrame(emissions, geometry = gpd.points_from_xy(emissions.LONGITUDE, emissions.LATITUDE, crs = 'EPSG:4326'))

In [5]:
# Focus Data

## Traffic

aadt = traffic[['SEQUENCE_N', 'ROUTE_LABE', 'CURRENT_VO', 'geometry']]
big_aadt = aadt[aadt['CURRENT_VO'] > 10000]

# Emissions

emissions_2020 = emissions_geo[emissions_geo['YEAR']==2020][['FACILITY_NAME', 'INDUSTRY_TYPE', 'NAICS_CODE', 'POLLUTANT', 'LBS_EMITTED','geometry']]
big_vocs = emissions_2020[(emissions_2020['POLLUTANT'] == 'Volatile Organic Compounds') & 
                         (emissions_2020['LBS_EMITTED'] > 1000)]
big_pm = emissions_2020[(emissions_2020['POLLUTANT'] == 'PM2.5 Primary') & 
                         (emissions_2020['LBS_EMITTED'] > 1000)]

# Define Visualizations

## Annual Average Daily Traffic

In [6]:
### AADT style

def style_aadt(feature):
    '''Set Thickness/color of streets to be proportional to traffic volume'''
    
    volume = feature['properties']['CURRENT_VO']
    
    if volume < 1773: # Low volume
        return {
        "weight": 0.5,
        "color": "#848484"
    }
    elif volume < 5378: # Low-mid volume
        return {
        "weight": 1,
        "color": "#936d6d"
    }
    elif volume < 16308: # Mid volume
        return {
        "weight": 2,
        "color": "#a94646"
    }
    elif volume < 100000: # High Volume
        return {
        "weight": 5,
        "color": "#f90707"
    }
    else: # Very High Volume Potentially could use another break here
        return {
        "weight": 10,
        "color": "#090707"
    }
    

## Permitted Emissions

### Popups

In [7]:
def emissions_popup_html(point):
    '''Creates a popup with basic info on an industrial polluter'''

    left_col_color = "#627c6a"
    right_col_color = "#bccdb9"
    
    html = """<!DOCTYPE html>
<html>

<head>
<h4 style="margin-bottom:10"; width="200px">{}</h4>""".format(point.FACILITY_NAME) + """

</head>
    <table style="height: 100px; width: 300px;">
<tbody>
<tr>
<td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;">Pollutant:</span></td>
<td style="width: 150px;background-color: """+ right_col_color +""";">{}</td>""".format(point.POLLUTANT) + """
</tr>
<tr>
<td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;">Pounds Emitted (2020):</span></td>
<td style="width: 150px;background-color: """+ right_col_color +""";">{}</td>""".format(point.LBS_EMITTED) + """
</tr>
<tr>
<td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;">Industry Type:</span></td>
<td style="width: 150px;background-color: """+ right_col_color +""";">{}</td>""".format(point.INDUSTRY_TYPE) + """
</tr>
<tr>
<td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;">NAICS code:</span></td>
<td style="width: 150px;background-color: """+ right_col_color +""";">{}</td>""".format(point.NAICS_CODE) + """
</tr>

</tbody>
</table>
</html>
"""
    return html

### VOC Emissions

In [8]:
# Plot the facilities' VOC emission
    
def plot_voc(point):
    '''plot circle of facilities related to amount of vocs emitted'''    
    
    lbs = point.LBS_EMITTED 
    
    if lbs < 25: # Low volume
        weight = 1,
        color = '#848484'
    elif lbs < 100: # Low-mid volume
        weight = 3,
        color = '#936d6d'
    elif lbs < 1000: # Mid volume
        weight = 5,
        color = '#a94646'
    elif lbs < 10000: # High Volume
        weight = 10,
        color = '#f90707'
    else: # Very High Volume
        weight = 15,
        color = '#090707'
        
    popup = emissions_popup_html(point)
        
    folium.Circle(location=[point.geometry.y,point.geometry.x],
                       weight = weight,
                       color = color,
                       fill = True,
                       popup = popup
                       ).add_to(voc_feature_group)

## PM2.5 Emissions

In [9]:
# Plot the facilities' VOC emission
    
def plot_pm(point):
    '''plot circle of facilities related to amount of particulate matter 2.5 emitted'''    
    
    lbs = point.LBS_EMITTED 
    
    if lbs < 25: # Low volume
        weight = 1,
        color = '#848484'
    elif lbs < 100: # Low-mid volume
        weight = 3,
        color = '#936d6d'
    elif lbs < 1000: # Mid volume
        weight = 5,
        color = '#a94646'
    elif lbs < 10000: # High Volume
        weight = 10,
        color = '#f90707'
    else: # Very High Volume
        weight = 15,
        color = '#090707'
        
    popup = emissions_popup_html(point)
        
    folium.Circle(location=[point.geometry.y,point.geometry.x],
                       weight = weight,
                       color = color,
                       fill = True,
                       popup = popup
                       ).add_to(pm_feature_group)

## Health and Census Data

In [10]:
# Focusing Health Data
health_focus = health[['GEOID10', 'ACCESS2_Cr', 'CANCER_Cru', 'CASTHMA_Cr', 'DEPRESSION', 'OBESITY_Cr', 'geometry']]

# Focusing Census Data
demo_focus = demo[['Income', 'Total_Coun', 'White_Coun', 'GEOID10', 'geometry']]

In [29]:
# Merge Health & Census Data

demo_focus['GEOID10'] = demo_focus['GEOID10'].astype(str) #changing the GEOID10 column to a string
health_focus['GEOID10'] = health_focus['GEOID10'].astype(str)

# Merge tracts and health, remove final two columns from health, renaming geometry_x to geometry

health_demo = pd.merge(health_focus, demo_focus,
                         left_on = 'GEOID10', right_on = 'GEOID10',
                         how = 'inner').iloc[:,0:108].rename(columns = {'geometry_x':'geometry'})
health_demo_full = health_demo.drop(columns=['geometry_y'])
health_demo_full.head(2)

GEOID10  ACCESS2_Cr  CANCER_Cru  CASTHMA_Cr  DEPRESSION  OBESITY_Cr  \
0  27053111300         5.8         6.5         7.6        21.4        22.5   
1  27053111200         6.5         5.8         7.8        22.4        22.8   

                                            geometry  Income  Total_Coun  \
0  POLYGON ((475529.871 4972059.890, 475431.109 4...   28163        3840   
1  POLYGON ((474027.281 4972606.106, 474027.178 4...   50288        4467   

   White_Coun  
0        2485  
1        3521

In [47]:
# Calculating area, population density, and percentages

health_demo_full['White_Per'] = ((health_demo_full['White_Coun']/health_demo_full['Total_Coun'])*100).fillna(0).astype(int)
health_demo_full['NonWhite_Per'] = (100 - (health_demo_full['White_Per'])).fillna(0).astype(int)

health_demo_area = health_demo_full.assign(area = (health_demo_full.area)/(1000**2))
health_demo_area['Pop_Dens'] = (health_demo_area['Total_Coun']/health_demo_area['area']).fillna(0).astype(int)
health_demo_area.sample(10)

GEOID10  ACCESS2_Cr  CANCER_Cru  CASTHMA_Cr  DEPRESSION  OBESITY_Cr  \
77  27053103700         9.3         3.6         8.5        23.1        20.2   
36  27053107600         8.7         5.9         8.4        23.6        24.2   
46  27053108700        12.7         5.6         9.0        23.6        27.6   
92  27053102600        14.1         3.8         9.1        24.2        26.6   
13  27053011000         8.2         5.3         8.2        23.0        24.0   
9   27053110500         8.3         7.7         7.7        21.3        23.6   
42  27053100700        13.4         4.5         9.5        23.8        28.7   
41  27053101300        21.3         4.2        11.4        23.4        35.0   
91  27053104000        12.6         2.4        10.1        26.6        22.6   
0   27053111300         5.8         6.5         7.6        21.4        22.5   

                                             geometry  Income  Total_Coun  \
77  POLYGON ((480194.186 4980742.685, 480176.935 4...   40715        5951   
36  POLYGON ((483416.411 4976472.980, 483321.892 4...   53247        2818   
46  POLYGON ((481235.466 4975658.847, 481184.415 4...   23760        3627   
92  POLYGON ((481811.584 4983234.803, 481803.789 4...   43782        3701   
13  POLYGON ((480479.985 4973655.100, 480449.918 4...  104207        6633   
9   POLYGON ((483725.110 4972863.095, 483723.227 4...   54437        3623   
42  POLYGON ((475611.577 4984468.343, 475512.372 4...   58243        3660   
41  POLYGON ((475667.877 4983464.994, 475610.310 4...   39751        4231   
91  POLYGON ((481728.723 4983252.036, 481762.362 4...   17244        5527   
0   POLYGON ((475529.871 4972059.890, 475431.109 4...   28163        3840   

    White_Coun  White_Per  NonWhite_Per      area  Pop_Dens  
77        5069         85            15  0.932903      6379  
36        2253         79            21  1.705058      1652  
46        1715         47            53  1.113084      3258  
92        3014         81            19  2.463128      1502  
13        6449         97             3  1.459270      4545  
9         3076         84            16  3.105422      1166  
42        3504         95             5  0.966021      3788  
41        3101         73            27  0.463658      9125  
91        1855         33            67  5.641942       979  
0         2485         64            36  1.774710      2163

In [43]:
# Setting style for popups
style_function = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0.1, 
                            'weight': 0.1}
highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}

# Population Density
popdens_feature_group = folium.FeatureGroup() # Create Feature Group
a = folium.Choropleth(health_demo_area, 
                  data = health_demo_area, # Get Data
                  key_on = 'feature.properties.GEOID10', # Select key
                  columns = ['GEOID10','Pop_Dens'], # Select column
                  fill_color = 'YlOrBr', # Choose colorscheme
                  legend_name = 'Population Density', # Name legend
                  overlay = True,
                  name = 'Population Density', # Name layer
                  show = False
                  )
# Removing legends
for key in a._children:
    if key.startswith('color_map'):
        del(a._children[key])
        

hover_a = folium.features.GeoJson(
    data = health_demo_area,
    style_function=style_function, 
    control=False,
    highlight_function=highlight_function, 
    popup=folium.features.GeoJsonPopup(
        fields=['Pop_Dens',
                'ACCESS2_Cr',
                'CANCER_Cru',
                'CASTHMA_Cr', 
                'DEPRESSION', 
                'OBESITY_Cr'
               ],
        aliases=['Population Density',
                 'No Access to Healthcare (%)', 
                 'Cancer (%)', 
                 'Asthma (%)', 
                 'Depression (%)', 
                 'Obesity (%)'                 
                 ],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)
a.add_child(hover_a)


# Race: White
white_feature_group = folium.FeatureGroup(name = 'Race: White',
                                           show = False) # Create Feature Group

b = folium.Choropleth(health_demo_area, 
                  data = health_demo_area, # Get Data
                  key_on = 'feature.properties.GEOID10', # Select key
                  columns = ['GEOID10','White_Per'], # Select column
                  fill_color = 'YlOrBr', # Choose colorscheme
                  legend_name = 'Race: White (%)', # Name legend
                  overlay = True,
                  name = 'Race: White', # Name layer
                  show = False
                  )
# Removing legends
for key in b._children:
    if key.startswith('color_map'):
        del(b._children[key])
        
hover_b = folium.features.GeoJson(
    data = health_demo_area,
    style_function=style_function, 
    control=False,
    highlight_function=highlight_function, 
    popup=folium.features.GeoJsonPopup(
        fields=['White_Per',
                'ACCESS2_Cr',
                'CANCER_Cru',
                'CASTHMA_Cr', 
                'DEPRESSION', 
                'OBESITY_Cr'
               ],
        aliases=['Race: White (%)',
                 'No Access to Healthcare (%)', 
                 'Cancer (%)', 
                 'Asthma (%)', 
                 'Depression (%)', 
                 'Obesity (%)'                 
                 ],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)
b.add_child(hover_b)


# Race: Non-White
nonwhite_feature_group = folium.FeatureGroup(name = 'Race: Non-White',
                                           show = False) # Create Feature Group

c = folium.Choropleth(health_demo_area, 
                  data = health_demo_area, # Get Data
                  key_on = 'feature.properties.GEOID10', # Select key
                  columns = ['GEOID10','NonWhite_Per'], # Select column
                  fill_color = 'YlOrBr', # Choose colorscheme
                  legend_name = 'Race: Non-White (%)', # Name legend
                  overlay = True,
                  name = 'Race: Non-White', # Name layer
                  show = False
                  )
# Removing legends
for key in c._children:
    if key.startswith('color_map'):
        del(c._children[key])

hover_c = folium.features.GeoJson(
    data = health_demo_area,
    style_function=style_function, 
    control=False,
    highlight_function=highlight_function, 
    popup=folium.features.GeoJsonPopup(
        fields=['NonWhite_Per',
                'ACCESS2_Cr',
                'CANCER_Cru',
                'CASTHMA_Cr', 
                'DEPRESSION', 
                'OBESITY_Cr'
               ],
        aliases=['Race: Non-White (%)',
                 'No Access to Healthcare (%)', 
                 'Cancer (%)', 
                 'Asthma (%)', 
                 'Depression (%)', 
                 'Obesity (%)'                 
                 ],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)
c.add_child(hover_c)

# Income
income_feature_group = folium.FeatureGroup(name = 'Average Income',
                                           show = False) # Create Feature Group

d = folium.Choropleth(health_demo_area, 
                  data = health_demo_area, # Get Data
                  key_on = 'feature.properties.GEOID10', # Select key
                  columns = ['GEOID10','Income'], # Select column
                  fill_color = 'YlOrBr', # Choose colorscheme
                  legend_name = 'Average Income ($)', # Name legend
                  overlay = True,
                  name = 'Average Income', # Name layer
                  show = False
                  )
# Removing legends
for key in d._children:
    if key.startswith('color_map'):
        del(d._children[key])

hover_d = folium.features.GeoJson(
    data = health_demo_area,
    style_function=style_function, 
    control=False,
    highlight_function=highlight_function, 
    popup=folium.features.GeoJsonPopup(
        fields=['Income',
                'ACCESS2_Cr',
                'CANCER_Cru',
                'CASTHMA_Cr', 
                'DEPRESSION', 
                'OBESITY_Cr'
               ],
        aliases=['Average Income',
                 'No Access to Healthcare (%)', 
                 'Cancer (%)', 
                 'Asthma (%)', 
                 'Depression (%)', 
                 'Obesity (%)'                 
                 ],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)
d.add_child(hover_d)

# Add to the map!

In [49]:
# Make a basic folium map

m = folium.Map(location=[44.986656, -93.258133],
               zoom_start=12,
               tiles = 'cartodbpositron',
               name = 'Mapping Green Zones')

# Add Minneapolis boundary

folium.GeoJson(mpls_boundary_path,
               style_function = lambda feature: {'color':'#000000', # Border color
                                                'fillOpacity' : '0'}, # Fill transparency
               name="Minneapolis Boundary", # Layer's Name
               control = False # Can you toggle in layer control?
              ).add_to(m)

# Add GZ boundaries

folium.GeoJson(gz_boundary_path, 
               style_function = lambda feature: {'fillColor':'#84E884',
                                 'color':'#003700',
                                 'fillOpacity': '0.5',
                                 'weight': '0'}, # Thickness of lines
               name = "Green Zone Boundaries",
               control = False).add_to(m)

# Add traffic

folium.GeoJson(big_aadt,
               style_function = lambda feature: style_aadt(feature), 
               name = 'Annual Average Daily Traffic',
               show = False # Does this appear in default of map
              ).add_to(m)

# Add Volatile Organic Compounds

voc_feature_group = folium.FeatureGroup(name = 'VOC Emitters',
                                           show = False) # Create Feature Group
big_vocs.apply(plot_voc, axis = 1) # Add to group
m.add_child(voc_feature_group)

# Add PM2.5

pm_feature_group = folium.FeatureGroup(name = 'PM2.5 Emitters',
                                           show = False) # Create Feature Group
big_pm.apply(plot_pm, axis = 1) # Add to group
m.add_child(pm_feature_group)

# Add Census Data

    #Population Density

m.add_child(a)    

    #Race: White

m.add_child(b)

    #Race: Non-White
    
m.add_child(c)

    #Income

m.add_child(d)


# Turn on layer control

m.add_child(folium.map.LayerControl())

In [ ]:
# Save Map

m.save(os.path.join('.', 'MVP.html'))